# Generating Genome Feature Tracks

In this notebook, I'll use the [NCBI assembly](https://www.ncbi.nlm.nih.gov/assembly/GCF_902806645.1/) and [NCBI Annotation Release 102](https://www.ncbi.nlm.nih.gov/genome/annotation_euk/Crassostrea_gigas/102/) to genome feature tracks for the Roslin *C. gigas* genome.

## 0. Set working directory and variables

In [1]:
!pwd

/Users/yaaminivenkataraman/Documents/ceabigr/code


In [2]:
#!mkdir ../genome-features/

In [3]:
cd ../genome-features/

/Users/yaaminivenkataraman/Documents/ceabigr/genome-features


In [3]:
!which bedtools

/opt/homebrew/bin/bedtools


In [4]:
bedtoolsDirectory = "/opt/homebrew/bin"

## 1. Download NCBI assembly

I downloaded the GFF from [this link](https://www.ncbi.nlm.nih.gov/genome/?term=txid6565[orgn]). Can also curl from FTP links [here](https://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/002/022/765/GCF_002022765.2_C_virginica-3.0/)

In [5]:
!head -n100 GCF_002022765.2_C_virginica-3.0_genomic.gff

##gff-version 3
#!gff-spec-version 1.21
#!processor NCBI annotwriter
#!genome-build C_virginica-3.0
#!genome-build-accession NCBI_Assembly:GCF_002022765.2
#!annotation-source NCBI Crassostrea virginica Annotation Release 100
##sequence-region NC_035780.1 1 65668440
##species https://www.ncbi.nlm.nih.gov/Taxonomy/Browser/wwwtax.cgi?id=6565
NC_035780.1	RefSeq	region	1	65668440	.	+	.	ID=NC_035780.1:1..65668440;Dbxref=taxon:6565;Name=1;chromosome=1;collection-date=22-Mar-2015;country=USA;gbkey=Src;genome=chromosome;isolate=RU13XGHG1-28;isolation-source=Rutgers Haskin Shellfish Research Laboratory inbred lines (NJ);mol_type=genomic DNA;tissue-type=whole sample
NC_035780.1	Gnomon	gene	13578	14594	.	+	.	ID=gene-LOC111116054;Dbxref=GeneID:111116054;Name=LOC111116054;gbkey=Gene;gene=LOC111116054;gene_biotype=lncRNA
NC_035780.1	Gnomon	lnc_RNA	13578	14594	.	+	.	ID=rna-XR_002636969.1;Parent=gene-LOC111116054;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;Name=XR_002636969.1;gbkey=ncRNA;gene=LOC111

## 2. Prepare for feature track creation

Before I pull out feature tracks, I need to know which databases were used for annotation, which features I can expect and how many of them there are, and identify chromosome lengths.

### 2a. Annotation information

In [9]:
#Database identifiers for extracting features
!cut -f2 GCF_002022765.2_C_virginica-3.0_genomic.gff | sort | uniq -c | tail

   1 ##sequence-region NC_035784.1 1 98698416
   1 ##sequence-region NC_035785.1 1 51258098
   1 ##sequence-region NC_035786.1 1 57830854
   1 ##sequence-region NC_035787.1 1 75944018
   1 ##sequence-region NC_035788.1 1 104168038
   1 ##sequence-region NC_035789.1 1 32650045
  11 ##species https://www.ncbi.nlm.nih.gov/Taxonomy/Browser/wwwtax.cgi?id=6565
1482188 Gnomon
29345 RefSeq
1739 tRNAscan-SE


In [10]:
#Count the number of unique features in the GFF
!cut -f3 GCF_002022765.2_C_virginica-3.0_genomic.gff | sort | uniq -c

   1 #!annotation-source NCBI Crassostrea virginica Annotation Release 100
   1 #!genome-build C_virginica-3.0
   1 #!genome-build-accession NCBI_Assembly:GCF_002022765.2
   1 #!gff-spec-version 1.21
   1 #!processor NCBI annotwriter
   1 ###
   1 ##gff-version 3
   1 ##sequence-region NC_007175.2 1 17244
   1 ##sequence-region NC_035780.1 1 65668440
   1 ##sequence-region NC_035781.1 1 61752955
   1 ##sequence-region NC_035782.1 1 77061148
   1 ##sequence-region NC_035783.1 1 59691872
   1 ##sequence-region NC_035784.1 1 98698416
   1 ##sequence-region NC_035785.1 1 51258098
   1 ##sequence-region NC_035786.1 1 57830854
   1 ##sequence-region NC_035787.1 1 75944018
   1 ##sequence-region NC_035788.1 1 104168038
   1 ##sequence-region NC_035789.1 1 32650045
  11 ##species https://www.ncbi.nlm.nih.gov/Taxonomy/Browser/wwwtax.cgi?id=6565
645368 CDS
29258 cDNA_match
731916 exon
38838 gene
4750 lnc_RNA
60201 mRNA
 667 pseudogene
   2 rRNA
  11 region
 587 tRNA
1674 transcript


### 2b. Chromosome lengths

In [11]:
#Obtained the full FASTA from this link: https://www.ncbi.nlm.nih.gov/genome/?term=txid6565[orgn]
#Check information
!head GCF_002022765.2_C_virginica-3.0_genomic.fna

>NC_035780.1 Crassostrea virginica isolate RU13XGHG1-28 chromosome 1, C_virginica-3.0, whole genome shotgun sequence
tgacacatatataaagttgaagTCCATACGTAAGAAACTCTGTGAGATATTAACCGAAAACCTTTTGAATCTTTacgaaa
aatatacatgttgcGCCAACTGGCGTAAATCAAAACCGGAAGCAGTAAGCATGTCGTGTTTAGTGTCTATCAAATGGACC
GGGGGAGTTCTAGTACATATCCAAAGATAAGGGCAATACATAAAATACTCGCAAAGTTATTGACCGtcaaagttgatgta
cttttagaaaaaaataatggaaaatgtggcTTTAGTGGAACGGCatcaatgtaaatttaaaatagcaggGTTTGCGTTTG
AATTAAAACATCGTGTTTGGTGTCGTTAGAAAGGTCTATTCCAGTTCTATAACATATCTAAAGGTCAGGTCAATCCgtta
atttataaaagagaTATGGGCGATCGCGGCATGAGTACTACATGACACAGAGTTACTTGCTCTTTGCTACTTCAGCGTTT
CCGGAAGCGTAGTTTTTTTCGTGCGTTTATTCCTTGCAGATAGCCAAGCAATTCCACAAGAATTGAACTCATTTGGCATT
AaacttcttgaaaaaataacaaattctttcttttctcatatCAGGTGGATgtcgagtactttgattctaccgggcataga
gtagcaacagtactttcagtaccgtgattttgctaccaatcataggactgaaagtactgtgtatagaccaatcacagtac


In [16]:
#Extract chr and sequence length information
!awk '$0 ~ ">" {print c; c=0;printf substr($0,2,14) "\t"; } $0 !~ ">" {c+=length($0);} END { print c; }' \
GCF_002022765.2_C_virginica-3.0_genomic.fna \
| sed 's/Cr//g' \
| awk '{print $1"\t"$2}' \
| tail -n +2 \
> C_virginica-3.0-sequence-lengths.txt

In [20]:
#11 chr total including mitochondrial information
!head -n11 C_virginica-3.0-sequence-lengths.txt

NC_035780.1	65668440
NC_035781.1	61752955
NC_035782.1	77061148
NC_035783.1	59691872
NC_035784.1	98698416
NC_035785.1	51258098
NC_035786.1	57830854
NC_035787.1	75944018
NC_035788.1	104168038
NC_035789.1	32650045
NC_007175.2	17244


In [33]:
#New file with chr names only
!cut -f1 C_virginica-3.0-sequence-lengths.txt \
> C_virginica-3.0-chr.txt

## 2. Generate genome feature tracks

I will extract CDS, exon, gene, lncRNA and mRNA tracks. I can then use those existing tracks to produce intron and  intergenic tracks, as well as 1 kb upstream and downstream flanking regions with `bedtools`. I will also use the RepeatMasker output from NCBI for my transposable element track.

In [31]:
!{bedtoolsDirectory}/bedtools --version

bedtools v2.30.0


### 2a. Gene

In [6]:
#Isolate gene entries from multiple annotation databses. Tab mus be included between database and feature
#Sort output for downstream use
#Include chromosome name information
!grep -e "Gnomon	gene" -e "RefSeq	gene" -e "tRNAscan-SE	gene" \
GCF_002022765.2_C_virginica-3.0_genomic.gff \
| {bedtoolsDirectory}/sortBed \
-faidx C_virginica-3.0-chr.txt \
> C_virginica-3.0-gene.gff

In [7]:
!head C_virginica-3.0-gene.gff
!wc -l C_virginica-3.0-gene.gff

NC_035780.1	Gnomon	gene	13578	14594	.	+	.	ID=gene-LOC111116054;Dbxref=GeneID:111116054;Name=LOC111116054;gbkey=Gene;gene=LOC111116054;gene_biotype=lncRNA
NC_035780.1	Gnomon	gene	28961	33324	.	+	.	ID=gene-LOC111126949;Dbxref=GeneID:111126949;Name=LOC111126949;gbkey=Gene;gene=LOC111126949;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	43111	66897	.	-	.	ID=gene-LOC111110729;Dbxref=GeneID:111110729;Name=LOC111110729;gbkey=Gene;gene=LOC111110729;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	85606	95254	.	-	.	ID=gene-LOC111112434;Dbxref=GeneID:111112434;Name=LOC111112434;gbkey=Gene;gene=LOC111112434;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	99840	106460	.	+	.	ID=gene-LOC111120752;Dbxref=GeneID:111120752;Name=LOC111120752;gbkey=Gene;gene=LOC111120752;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	108305	110077	.	-	.	ID=gene-LOC111128944;Dbxref=GeneID:111128944;Name=LOC111128944;gbkey=Gene;gene=LOC111128944;gene_biotype=protein_coding;partial=true;start_range=.,108305

### 2b. CDS

In [8]:
!grep -e "Gnomon	CDS" -e "RefSeq	CDS" -e "tRNAscan-SE	CDS" \
GCF_002022765.2_C_virginica-3.0_genomic.gff \
| {bedtoolsDirectory}/sortBed \
-faidx C_virginica-3.0-chr.txt \
> C_virginica-3.0-CDS.gff

In [9]:
!head C_virginica-3.0-CDS.gff
!wc -l C_virginica-3.0-CDS.gff

NC_035780.1	Gnomon	CDS	30535	31557	.	+	0	ID=cds-XP_022327646.1;Parent=rna-XM_022471938.1;Dbxref=GeneID:111126949,Genbank:XP_022327646.1;Name=XP_022327646.1;gbkey=CDS;gene=LOC111126949;product=UNC5C-like protein;protein_id=XP_022327646.1
NC_035780.1	Gnomon	CDS	31736	31887	.	+	0	ID=cds-XP_022327646.1;Parent=rna-XM_022471938.1;Dbxref=GeneID:111126949,Genbank:XP_022327646.1;Name=XP_022327646.1;gbkey=CDS;gene=LOC111126949;product=UNC5C-like protein;protein_id=XP_022327646.1
NC_035780.1	Gnomon	CDS	31977	32565	.	+	1	ID=cds-XP_022327646.1;Parent=rna-XM_022471938.1;Dbxref=GeneID:111126949,Genbank:XP_022327646.1;Name=XP_022327646.1;gbkey=CDS;gene=LOC111126949;product=UNC5C-like protein;protein_id=XP_022327646.1
NC_035780.1	Gnomon	CDS	32959	33204	.	+	0	ID=cds-XP_022327646.1;Parent=rna-XM_022471938.1;Dbxref=GeneID:111126949,Genbank:XP_022327646.1;Name=XP_022327646.1;gbkey=CDS;gene=LOC111126949;product=UNC5C-like protein;protein_id=XP_022327646.1
NC_035780.1	Gnomon	CDS	43262	44358	.	-	2	ID=cds-XP_0

### 2c. Exon

In [10]:
!grep -e "Gnomon	exon" -e "RefSeq	exon" -e "tRNAscan-SE	exon" \
GCF_002022765.2_C_virginica-3.0_genomic.gff \
| {bedtoolsDirectory}/sortBed \
-faidx C_virginica-3.0-chr.txt \
> C_virginica-3.0-exon.gff

In [11]:
!head C_virginica-3.0-exon.gff
!wc -l C_virginica-3.0-exon.gff

NC_035780.1	Gnomon	exon	13578	13603	.	+	.	ID=exon-XR_002636969.1-1;Parent=rna-XR_002636969.1;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;gbkey=ncRNA;gene=LOC111116054;product=uncharacterized LOC111116054;transcript_id=XR_002636969.1
NC_035780.1	Gnomon	exon	14237	14290	.	+	.	ID=exon-XR_002636969.1-2;Parent=rna-XR_002636969.1;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;gbkey=ncRNA;gene=LOC111116054;product=uncharacterized LOC111116054;transcript_id=XR_002636969.1
NC_035780.1	Gnomon	exon	14557	14594	.	+	.	ID=exon-XR_002636969.1-3;Parent=rna-XR_002636969.1;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;gbkey=ncRNA;gene=LOC111116054;product=uncharacterized LOC111116054;transcript_id=XR_002636969.1
NC_035780.1	Gnomon	exon	28961	29073	.	+	.	ID=exon-XM_022471938.1-1;Parent=rna-XM_022471938.1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;gbkey=mRNA;gene=LOC111126949;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	Gnomon	exon	30524	31557	.	+	.	ID=exon-XM_022471938.1-2;

### 2d. lncRNA

In [12]:
!grep -e "Gnomon	lnc_RNA" -e "RefSeq	lnc_RNA" -e "tRNAscan-SE	lnc_RNA" \
GCF_002022765.2_C_virginica-3.0_genomic.gff \
| {bedtoolsDirectory}/sortBed \
-faidx C_virginica-3.0-chr.txt \
> C_virginica-3.0-lncRNA.gff

In [13]:
!head C_virginica-3.0-lncRNA.gff
!wc -l C_virginica-3.0-lncRNA.gff

NC_035780.1	Gnomon	lnc_RNA	13578	14594	.	+	.	ID=rna-XR_002636969.1;Parent=gene-LOC111116054;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;Name=XR_002636969.1;gbkey=ncRNA;gene=LOC111116054;model_evidence=Supporting evidence includes similarity to: 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 1 sample with support for all annotated introns;product=uncharacterized LOC111116054;transcript_id=XR_002636969.1
NC_035780.1	Gnomon	lnc_RNA	169468	170178	.	-	.	ID=rna-XR_002635081.1;Parent=gene-LOC111105702;Dbxref=GeneID:111105702,Genbank:XR_002635081.1;Name=XR_002635081.1;gbkey=ncRNA;gene=LOC111105702;model_evidence=Supporting evidence includes similarity to: 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 3 samples with support for all annotated introns;product=uncharacterized LOC111105702;transcript_id=XR_002635081.1
NC_035780.1	Gnomon	lnc_RNA	900326	903430	.	+	.	ID=rna-XR_002636046.1;Parent=gene-LOC111111519;Dbxref=GeneID

### 2e. mRNA

In [14]:
!grep -e "Gnomon	mRNA" -e "RefSeq	mRNA" -e "tRNAscan-SE	mRNA" \
GCF_002022765.2_C_virginica-3.0_genomic.gff \
| {bedtoolsDirectory}/sortBed \
-faidx C_virginica-3.0-chr.txt \
> C_virginica-3.0-mRNA.gff

In [15]:
!head C_virginica-3.0-mRNA.gff
!wc -l C_virginica-3.0-mRNA.gff

NC_035780.1	Gnomon	mRNA	28961	33324	.	+	.	ID=rna-XM_022471938.1;Parent=gene-LOC111126949;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	Gnomon	mRNA	43111	66897	.	-	.	ID=rna-XM_022447324.1;Parent=gene-LOC111110729;Dbxref=GeneID:111110729,Genbank:XM_022447324.1;Name=XM_022447324.1;gbkey=mRNA;gene=LOC111110729;model_evidence=Supporting evidence includes similarity to: 1 Protein%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments;product=FMRFamide receptor-like%2C transcript variant X1;transcript_id=XM_022447324.1
NC_035780.1	Gnomon	mRNA	43111	46506	.	-	.	ID=rna-XM_022447333.1;Parent=gene-LOC111110729;Dbxref=GeneID:111110729,Genbank:XM_02244733

### 2f. Non-coding sequences

In [16]:
#Find the complement to the exon track (non-coding sequences)
#Create a BEDfile of IGV
!{bedtoolsDirectory}/complementBed \
-i C_virginica-3.0-exon.gff \
-g C_virginica-3.0-sequence-lengths.txt \
> C_virginica-3.0-nonCDS.bed

In [17]:
!head C_virginica-3.0-nonCDS.bed
!wc -l C_virginica-3.0-nonCDS.bed

NC_035780.1	0	13577
NC_035780.1	13603	14236
NC_035780.1	14290	14556
NC_035780.1	14594	28960
NC_035780.1	29073	30523
NC_035780.1	31557	31735
NC_035780.1	31887	31976
NC_035780.1	32565	32958
NC_035780.1	33324	43110
NC_035780.1	44358	45912
  337305 C_virginica-3.0-nonCDS.bed


### 2g. Intron

In [18]:
#Find the intersection between the non-coding sequences and genes (introns)
!{bedtoolsDirectory}/intersectBed \
-a C_virginica-3.0-nonCDS.bed \
-b C_virginica-3.0-gene.gff -sorted \
> C_virginica-3.0-intron.bed

In [19]:
!head C_virginica-3.0-intron.bed
!wc -l C_virginica-3.0-intron.bed

NC_035780.1	13603	14236
NC_035780.1	14290	14556
NC_035780.1	29073	30523
NC_035780.1	31557	31735
NC_035780.1	31887	31976
NC_035780.1	32565	32958
NC_035780.1	44358	45912
NC_035780.1	46506	64122
NC_035780.1	64334	66868
NC_035780.1	85777	88422
  311341 C_virginica-3.0-intron.bed


### 2h. Untranslated regions of exons

In [20]:
#Obtain UTRs by subtracting CDS from exons
!{bedtoolsDirectory}/subtractBed \
-a C_virginica-3.0-exon.gff \
-b C_virginica-3.0-CDS.gff \
-sorted \
-g C_virginica-3.0-sequence-lengths.txt \
> C_virginica-3.0-exonUTR.gff

In [21]:
!head C_virginica-3.0-exonUTR.gff
!wc -l C_virginica-3.0-exonUTR.gff

NC_035780.1	Gnomon	exon	13578	13603	.	+	.	ID=exon-XR_002636969.1-1;Parent=rna-XR_002636969.1;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;gbkey=ncRNA;gene=LOC111116054;product=uncharacterized LOC111116054;transcript_id=XR_002636969.1
NC_035780.1	Gnomon	exon	14237	14290	.	+	.	ID=exon-XR_002636969.1-2;Parent=rna-XR_002636969.1;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;gbkey=ncRNA;gene=LOC111116054;product=uncharacterized LOC111116054;transcript_id=XR_002636969.1
NC_035780.1	Gnomon	exon	14557	14594	.	+	.	ID=exon-XR_002636969.1-3;Parent=rna-XR_002636969.1;Dbxref=GeneID:111116054,Genbank:XR_002636969.1;gbkey=ncRNA;gene=LOC111116054;product=uncharacterized LOC111116054;transcript_id=XR_002636969.1
NC_035780.1	Gnomon	exon	28961	29073	.	+	.	ID=exon-XM_022471938.1-1;Parent=rna-XM_022471938.1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;gbkey=mRNA;gene=LOC111126949;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	Gnomon	exon	30524	30534	.	+	.	ID=exon-XM_022471938.1-2;

### 2i. Flanking regions (1 kb)

#### All flanks

In [22]:
#Create 1 kb flanking regions
#Subtract existing genes from artificial flanks
!{bedtoolsDirectory}/flankBed \
-i C_virginica-3.0-gene.gff \
-g C_virginica-3.0-sequence-lengths.txt \
-b 1000 \
| {bedtoolsDirectory}/subtractBed \
-a - \
-b C_virginica-3.0-gene.gff \
> C_virginica-3.0-flanks.gff

In [23]:
!head C_virginica-3.0-flanks.gff
!wc -l C_virginica-3.0-flanks.gff

NC_035780.1	Gnomon	gene	12578	13577	.	+	.	ID=gene-LOC111116054;Dbxref=GeneID:111116054;Name=LOC111116054;gbkey=Gene;gene=LOC111116054;gene_biotype=lncRNA
NC_035780.1	Gnomon	gene	14595	15594	.	+	.	ID=gene-LOC111116054;Dbxref=GeneID:111116054;Name=LOC111116054;gbkey=Gene;gene=LOC111116054;gene_biotype=lncRNA
NC_035780.1	Gnomon	gene	27961	28960	.	+	.	ID=gene-LOC111126949;Dbxref=GeneID:111126949;Name=LOC111126949;gbkey=Gene;gene=LOC111126949;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	33325	34324	.	+	.	ID=gene-LOC111126949;Dbxref=GeneID:111126949;Name=LOC111126949;gbkey=Gene;gene=LOC111126949;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	42111	43110	.	-	.	ID=gene-LOC111110729;Dbxref=GeneID:111110729;Name=LOC111110729;gbkey=Gene;gene=LOC111110729;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	66898	67897	.	-	.	ID=gene-LOC111110729;Dbxref=GeneID:111110729;Name=LOC111110729;gbkey=Gene;gene=LOC111110729;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	84606	85605	.	-	.	ID

#### Upstream flanks

In [24]:
#Create 1 kb upstream flanking regions (-l) based on strand (-s)
#Subtract existing genes from artificial flanks
!{bedtoolsDirectory}/flankBed \
-i C_virginica-3.0-gene.gff \
-g C_virginica-3.0-sequence-lengths.txt \
-l 1000 \
-r 0 \
-s \
| {bedtoolsDirectory}/subtractBed \
-a - \
-b C_virginica-3.0-gene.gff \
> C_virginica-3.0-upstream.gff

In [25]:
!head C_virginica-3.0-upstream.gff
!wc -l C_virginica-3.0-upstream.gff

NC_035780.1	Gnomon	gene	12578	13577	.	+	.	ID=gene-LOC111116054;Dbxref=GeneID:111116054;Name=LOC111116054;gbkey=Gene;gene=LOC111116054;gene_biotype=lncRNA
NC_035780.1	Gnomon	gene	27961	28960	.	+	.	ID=gene-LOC111126949;Dbxref=GeneID:111126949;Name=LOC111126949;gbkey=Gene;gene=LOC111126949;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	66898	67897	.	-	.	ID=gene-LOC111110729;Dbxref=GeneID:111110729;Name=LOC111110729;gbkey=Gene;gene=LOC111110729;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	95255	96254	.	-	.	ID=gene-LOC111112434;Dbxref=GeneID:111112434;Name=LOC111112434;gbkey=Gene;gene=LOC111112434;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	98840	99839	.	+	.	ID=gene-LOC111120752;Dbxref=GeneID:111120752;Name=LOC111120752;gbkey=Gene;gene=LOC111120752;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	110078	111077	.	-	.	ID=gene-LOC111128944;Dbxref=GeneID:111128944;Name=LOC111128944;gbkey=Gene;gene=LOC111128944;gene_biotype=protein_coding;partial=true;start_range=.,108305


#### Downstream flanks

In [26]:
#Create 1 kb upstream flanking regions (-l) based on strand (-s)
#Subtract existing genes from artificial flanks
!{bedtoolsDirectory}/flankBed \
-i C_virginica-3.0-gene.gff \
-g C_virginica-3.0-sequence-lengths.txt \
-l 0 \
-r 1000 \
-s \
| {bedtoolsDirectory}/subtractBed \
-a - \
-b C_virginica-3.0-gene.gff \
> C_virginica-3.0-downstream.gff

In [27]:
!head C_virginica-3.0-downstream.gff
!wc -l C_virginica-3.0-downstream.gff

NC_035780.1	Gnomon	gene	14595	15594	.	+	.	ID=gene-LOC111116054;Dbxref=GeneID:111116054;Name=LOC111116054;gbkey=Gene;gene=LOC111116054;gene_biotype=lncRNA
NC_035780.1	Gnomon	gene	33325	34324	.	+	.	ID=gene-LOC111126949;Dbxref=GeneID:111126949;Name=LOC111126949;gbkey=Gene;gene=LOC111126949;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	42111	43110	.	-	.	ID=gene-LOC111110729;Dbxref=GeneID:111110729;Name=LOC111110729;gbkey=Gene;gene=LOC111110729;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	84606	85605	.	-	.	ID=gene-LOC111112434;Dbxref=GeneID:111112434;Name=LOC111112434;gbkey=Gene;gene=LOC111112434;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	106461	107460	.	+	.	ID=gene-LOC111120752;Dbxref=GeneID:111120752;Name=LOC111120752;gbkey=Gene;gene=LOC111120752;gene_biotype=protein_coding
NC_035780.1	Gnomon	gene	107305	108304	.	-	.	ID=gene-LOC111128944;Dbxref=GeneID:111128944;Name=LOC111128944;gbkey=Gene;gene=LOC111128944;gene_biotype=protein_coding;partial=true;start_range=.,10830

### 2j. Intergenic regions

In [28]:
#Find the complement of genes, then subtract flanks to obtain intergenic regions
!{bedtoolsDirectory}/complementBed \
-i C_virginica-3.0-gene.gff -sorted \
-g C_virginica-3.0-sequence-lengths.txt \
| {bedtoolsDirectory}/subtractBed \
-a - \
-b C_virginica-3.0-flanks.gff \
> C_virginica-3.0-intergenic.bed

In [29]:
!head C_virginica-3.0-intergenic.bed
!wc -l C_virginica-3.0-intergenic.bed

NC_035780.1	0	12577
NC_035780.1	15594	27960
NC_035780.1	34324	42110
NC_035780.1	67897	84605
NC_035780.1	96254	98839
NC_035780.1	111077	150858
NC_035780.1	158536	162808
NC_035780.1	184798	189448
NC_035780.1	194594	203242
NC_035780.1	208743	213890
   23949 C_virginica-3.0-intergenic.bed


### 2k. Transposable elements

In [30]:
!curl https://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/002/022/765/GCF_002022765.2_C_virginica-3.0/GCF_002022765.2_C_virginica-3.0_rm.out.gz \
> C_virginica-3.0-rm.te.gz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 8847k  100 8847k    0     0  3621k      0  0:00:02  0:00:02 --:--:-- 3623k


In [31]:
!gunzip -k C_virginica-3.0-rm.te.gz

In [32]:
!head C_virginica-3.0-rm.te

   SW     perc    perc    perc  query           position in query                   matching       repeat           position in repeat
score     div.    del.    ins.  sequence        begin      end             (left)   repeat         class/family   begin  end    (left)     ID

   71    0.000   0.000   0.000  NC_035780.1           1473       1535  (65666905) + (TAACCC)n      Simple_repeat       1     63    (0)      1
   13   14.100   0.000   6.100  NC_035780.1           8261       8295  (65660145) + (CTCCT)n       Simple_repeat       1     33    (0)      2
   23   18.900   0.000   0.000  NC_035780.1          10552      10600  (65657840) + (TGAA)n        Simple_repeat       1     49    (0)      3
   37    0.000   0.000   0.000  NC_035780.1          11265      11298  (65657142) + (AAG)n         Simple_repeat       1     34    (0)      4
   72    0.000   0.000   0.000  NC_035780.1          12211      12271  (65656169) + (AG)n          Simple_repeat       1     61    (0)      5
   14   21.4

In [33]:
#Convert RepeatMasker output to a BEDfile
#Skip the first 4 lines 
#Print columns 5-7 as a tab-delimited output
!tail -n +4 C_virginica-3.0-rm.te \
| awk 'BEGIN{OFS= "\t"} {print $5, $6, $7}' \
> C_virginica-3.0-rm.te.bed

In [34]:
!head C_virginica-3.0-rm.te.bed
!wc -l C_virginica-3.0-rm.te.bed

NC_035780.1	1473	1535
NC_035780.1	8261	8295
NC_035780.1	10552	10600
NC_035780.1	11265	11298
NC_035780.1	12211	12271
NC_035780.1	15431	15484
NC_035780.1	15520	15552
NC_035780.1	15585	15619
NC_035780.1	16397	16434
NC_035780.1	16631	16653
  344267 C_virginica-3.0-rm.te.bed


### 2k. C->T SNPs

In [7]:
!find ../output/methylation-landscape/*vcf

../output/methylation-landscape/12M_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/13M_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/16F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/19F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/22F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/23M_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/29F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/31M_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/35F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/36F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/39F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/3F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/methylation-landscape/41F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
../output/met

In [19]:
%%bash

for f in ../output/methylation-landscape/*vcf
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b C_virginica-3.0-fuzznuc-CGmotif.gff \
    | grep "C	T" \
    > ${f}_CT-SNPs.tab
    head ${f}_CT-SNPs.tab
    wc -l ${f}_CT-SNPs.tab
done

NC_035780.1	32910	.	C	T	1000	PASS	DP=56;ADF=0,0;ADR=35,21;AD=35,21;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:56:0,0:35,21:35,21:0,0,28,0,0,21,35,0:0,0,36,0,0,36,36,0:0.625,0.375
NC_035780.1	33152	.	C	T	1000	PASS	DP=50;ADF=0,0;ADR=25,25;AD=25,25;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:50:0,0:25,25:25,25:0,0,39,0,0,25,25,0:0,0,35,0,0,36,37,0:0.500,0.500
NC_035780.1	39853	.	C	T	1000	PASS	DP=80;ADF=0,0;ADR=48,32;AD=48,32;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:80:0,0:48,32:48,32:0,0,56,0,0,32,48,0:0,0,37,0,0,36,36,0:0.600,0.400
NC_035780.1	80456	.	C	T	108	PASS	DP=37;ADF=0,0;ADR=28,9;AD=28,9;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:37:0,0:28,9:28,9:0,0,38,0,0,9,28,0:0,0,36,0,0,36,36,0:0.757,0.243
NC_035780.1	80703	.	C	T	1000	PASS	DP=25;ADF=0,0;ADR=0,25;AD=0,25;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:25:0,0:0,25:0,25:0,0,14,0,0,25,0,0:0,0,36,0,0,37,0,0:0.000,1.000
NC_035780.1	90833	.	C	T	1000	Low	DP=7;ADF=0,0;ADR=0,7;AD=0,7;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:7:0,0:0,7:0,7:0,0,23,0,0,7,0,0:0,0,36,0,0,37,0,0:0.000,1.000


In [23]:
%%bash

for f in ../output/methylation-landscape/*CT-SNPs.tab
do
    [ -f ${f} ] || continue
    mv "${f}" "${f//_R1_val_1_bismark_bt2_pe.SNP-results.vcf/}"

done

In [24]:
!find ../output/methylation-landscape/*CT-SNPs.tab

../output/methylation-landscape/12M_CT-SNPs.tab
../output/methylation-landscape/13M_CT-SNPs.tab
../output/methylation-landscape/16F_CT-SNPs.tab
../output/methylation-landscape/19F_CT-SNPs.tab
../output/methylation-landscape/22F_CT-SNPs.tab
../output/methylation-landscape/23M_CT-SNPs.tab
../output/methylation-landscape/29F_CT-SNPs.tab
../output/methylation-landscape/31M_CT-SNPs.tab
../output/methylation-landscape/35F_CT-SNPs.tab
../output/methylation-landscape/36F_CT-SNPs.tab
../output/methylation-landscape/39F_CT-SNPs.tab
../output/methylation-landscape/3F_CT-SNPs.tab
../output/methylation-landscape/41F_CT-SNPs.tab
../output/methylation-landscape/44F_CT-SNPs.tab
../output/methylation-landscape/48M_CT-SNPs.tab
../output/methylation-landscape/50F_CT-SNPs.tab
../output/methylation-landscape/52F_CT-SNPs.tab
../output/methylation-landscape/53F_CT-SNPs.tab
../output/methylation-landscape/54F_CT-SNPs.tab
../output/methylation-landscape/59M_CT-SNPs.tab
../output/methylation-landscape/64M_CT-SN

In [26]:
#Combine C/T SNPs into one file
!cat ../output/methylation-landscape/*CT-SNPs.tab >> all-CT-SNPs.tab
!head all-CT-SNPs.tab
!wc -l all-CT-SNPs.tab

NC_035780.1	32910	.	C	T	1000	PASS	DP=56;ADF=0,0;ADR=35,21;AD=35,21;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:56:0,0:35,21:35,21:0,0,28,0,0,21,35,0:0,0,36,0,0,36,36,0:0.625,0.375
NC_035780.1	33152	.	C	T	1000	PASS	DP=50;ADF=0,0;ADR=25,25;AD=25,25;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:50:0,0:25,25:25,25:0,0,39,0,0,25,25,0:0,0,35,0,0,36,37,0:0.500,0.500
NC_035780.1	39853	.	C	T	1000	PASS	DP=80;ADF=0,0;ADR=48,32;AD=48,32;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:80:0,0:48,32:48,32:0,0,56,0,0,32,48,0:0,0,37,0,0,36,36,0:0.600,0.400
NC_035780.1	80456	.	C	T	108	PASS	DP=37;ADF=0,0;ADR=28,9;AD=28,9;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:37:0,0:28,9:28,9:0,0,38,0,0,9,28,0:0,0,36,0,0,36,36,0:0.757,0.243
NC_035780.1	80703	.	C	T	1000	PASS	DP=25;ADF=0,0;ADR=0,25;AD=0,25;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:25:0,0:0,25:0,25:0,0,14,0,0,25,0,0:0,0,36,0,0,37,0,0:0.000,1.000
NC_035780.1	90833	.	C	T	1000	Low	DP=7;ADF=0,0;ADR=0,7;AD=0,7;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:7:0,0:0,7:0,7:0,0,23,0,0,7,0,0:0,0,36,0,0,37,0,0:0.000,1.000


In [27]:
#Take columns 1-5
#Sort combined C/T SNPs
#Only keep unique SNPs
!awk '{print $1"\t"$2"\t"$3"\t"$4"\t"$5}' all-CT-SNPs.tab \
| sort \
| uniq \
> unique-CT-SNPs.tab
!head unique-CT-SNPs.tab
!wc -l unique-CT-SNPs.tab

NC_007175.2	12774	.	C	T
NC_007175.2	15486	.	C	T
NC_007175.2	16441	.	C	T
NC_007175.2	2608	.	C	T
NC_007175.2	6075	.	C	T
NC_007175.2	6169	.	C	T
NC_007175.2	6742	.	C	T
NC_007175.2	7069	.	C	T
NC_007175.2	7089	.	C	T
NC_007175.2	7898	.	C	T
  517245 unique-CT-SNPs.tab


## 3. CG motifs

### 3a. Count CGs

In [73]:
#Obtain a rough count of CGs in the genome
!fgrep -o -i CG GCF_002022765.2_C_virginica-3.0_genomic.fna \
| wc -l

 14277725


Generated CG motif track with `fuzznuc` on [Galaxy](usegalaxy.org)

![Screen Shot 2022-05-11 at 6 58 51 PM](https://user-images.githubusercontent.com/22335838/167960980-73121d80-0aff-45e3-a156-febef79bc2d3.png)

In [ ]:
#Check Galaxy output
!head C_virginica-3.0-fuzznuc-CGmotif.gff
!wc -l C_virginica-3.0-fuzznuc-CGmotif.gff

##gff-version 2.0
##date 2022-05-11
##Type DNA NC_035780.1
NC_035780.1	fuzznuc	misc_feature	29	30	2.000	+	.	Sequence "NC_035780.1.1" ; note "*pat pattern1"
NC_035780.1	fuzznuc	misc_feature	55	56	2.000	+	.	Sequence "NC_035780.1.2" ; note "*pat pattern1"
NC_035780.1	fuzznuc	misc_feature	76	77	2.000	+	.	Sequence "NC_035780.1.3" ; note "*pat pattern1"
NC_035780.1	fuzznuc	misc_feature	94	95	2.000	+	.	Sequence "NC_035780.1.4" ; note "*pat pattern1"
NC_035780.1	fuzznuc	misc_feature	104	105	2.000	+	.	Sequence "NC_035780.1.5" ; note "*pat pattern1"
NC_035780.1	fuzznuc	misc_feature	117	118	2.000	+	.	Sequence "NC_035780.1.6" ; note "*pat pattern1"
NC_035780.1	fuzznuc	misc_feature	135	136	2.000	+	.	Sequence "NC_035780.1.7" ; note "*pat pattern1"


### 3b. Count CG overlaps with all genome feature tracks

In [75]:
#Genes
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-gene.gff \
| wc -l

 7778105


In [76]:
#CDS
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-CDS.gff \
| wc -l

 1728303


In [77]:
#Exon
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-exon.gff \
| wc -l

 2334303


In [78]:
#lncRNA
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-lncRNA.gff \
| wc -l

  281715


In [79]:
#mRNA
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-mRNA.gff \
| wc -l

 7507167


In [80]:
#nonCDS
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-nonCDS.bed \
| wc -l

 12138514


In [81]:
#Introns
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-intron.bed \
| wc -l

 5497597


In [82]:
#Exon UTR
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-exonUTR.gff \
| wc -l

  606308


In [83]:
#Upstream flanks
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-upstream.gff \
| wc -l

  694265


In [84]:
#Downstream flanks
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-downstream.gff \
| wc -l

  616684


In [85]:
#Intergenic regions
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-intergenic.bed \
| wc -l

 5417334


In [86]:
#Transposable elements
!{bedtoolsDirectory}/intersectBed \
-u \
-a C_virginica-3.0-fuzznuc-CGmotif.gff \
-b C_virginica-3.0-rm.te.bed \
| wc -l

  611471
